In [1]:
import math
import numpy as np
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go
from data import get_prices
from plotly.subplots import make_subplots
from typing import Any

In [2]:
get_prices(3, 0)

day  timestamp       product  bid_price_1  bid_volume_1  bid_price_2  \
0        0          0     CHOCOLATE         7999           111          NaN   
1        0          0  STRAWBERRIES         3999           210          NaN   
2        0          0         ROSES        14999            72          NaN   
3        0          0   GIFT_BASKET        71348            19      71347.0   
4        0        100   GIFT_BASKET        71344             1      71343.0   
...    ...        ...           ...          ...           ...          ...   
39995    0     999800   GIFT_BASKET        71131            19      71130.0   
39996    0     999900     CHOCOLATE         7987           124          NaN   
39997    0     999900   GIFT_BASKET        71117             2      71116.0   
39998    0     999900         ROSES        14550            18      14549.0   
39999    0     999900  STRAWBERRIES         4030           183          NaN   

       bid_volume_2  bid_price_3  bid_volume_3  ask_price_1  ask_volume_1  \
0               NaN          NaN           NaN         8001           111   
1               NaN          NaN           NaN         4001           210   
2               NaN          NaN           NaN        15001            72   
3              24.0          NaN           NaN        71362            19   
4              12.0      71342.0          20.0        71355             1   
...             ...          ...           ...          ...           ...   
39995          21.0          NaN           NaN        71145            19   
39996           NaN          NaN           NaN         7989           124   
39997          16.0      71115.0          18.0        71128             2   
39998          46.0          NaN           NaN        14551            64   
39999           NaN          NaN           NaN         4031            81   

       ask_price_2  ask_volume_2  ask_price_3  ask_volume_3  mid_price  \
0              NaN           NaN          NaN           NaN     8000.0   
1              NaN           NaN          NaN           NaN     4000.0   
2              NaN           NaN          NaN           NaN    15000.0   
3          71363.0          24.0          NaN           NaN    71355.0   
4          71356.0          12.0      71357.0          20.0    71349.5   
...            ...           ...          ...           ...        ...   
39995      71146.0          21.0          NaN           NaN    71138.0   
39996          NaN           NaN          NaN           NaN     7988.0   
39997      71130.0          16.0      71131.0          18.0    71122.5   
39998          NaN           NaN          NaN           NaN    14550.5   
39999       4032.0         102.0          NaN           NaN     4030.5   

       profit_and_loss  
0                  0.0  
1                  0.0  
2                  0.0  
3                  0.0  
4                  0.0  
...                ...  
39995              0.0  
39996              0.0  
39997              0.0  
39998              0.0  
39999              0.0  

[40000 rows x 17 columns]

In [9]:
def get_popular_price(row: Any, bid_ask: str) -> int:
    best_price = -1
    max_volume = -1

    for i in range(1, 4):
        volume = getattr(row, f"{bid_ask}_volume_{i}")
        if math.isnan(volume):
            break

        if volume > max_volume:
            best_price = getattr(row, f"{bid_ask}_price_{i}")
            max_volume = volume

    return best_price

def get_product_prices(prices: pd.DataFrame, product: str) -> np.ndarray:
    prices = prices[prices["product"] == product]

    mid_prices = []
    for row in prices.itertuples():
        popular_buy_price = get_popular_price(row, "bid")
        popular_sell_price = get_popular_price(row, "ask")
        mid_prices.append((popular_buy_price + popular_sell_price) / 2)

    return np.array(mid_prices)

all_chocolate = np.array([])
all_strawberries = np.array([])
all_roses = np.array([])
all_gift_basket = np.array([])

for day in range(4):
    prices = get_prices(3, day)

    chocolate = get_product_prices(prices, "CHOCOLATE")
    strawberries = get_product_prices(prices, "STRAWBERRIES")
    roses = get_product_prices(prices, "ROSES")
    gift_basket = get_product_prices(prices, "GIFT_BASKET")

    gift_basket_contents = 4 * chocolate + 6 * strawberries + roses
    gift_basket_diff = gift_basket - gift_basket_contents

    all_chocolate = np.concatenate([all_chocolate, chocolate])
    all_strawberries = np.concatenate([all_strawberries, strawberries])
    all_roses = np.concatenate([all_roses, roses])
    all_gift_basket = np.concatenate([all_gift_basket, gift_basket])

    buy_signal = gift_basket_diff < 355 * 0.9
    sell_signal = gift_basket_diff > 355 * 1.1

    gift_basket_diff_min = np.full_like(gift_basket_diff, gift_basket_diff.min())
    gift_basket_diff_max = np.full_like(gift_basket_diff, gift_basket_diff.max())
    gift_basket_diff_25 = np.full_like(gift_basket_diff, np.percentile(gift_basket_diff, 25))
    gift_basket_diff_75 = np.full_like(gift_basket_diff, np.percentile(gift_basket_diff, 75))

    fig = make_subplots(specs=[[{"secondary_y": True}]])
    fig.add_trace(go.Scatter(y=gift_basket, name="Gift Basket"), secondary_y=False)
    # fig.add_trace(go.Scatter(y=buy_signal.astype(int), name="Buy"), secondary_y=True)
    # fig.add_trace(go.Scatter(y=sell_signal.astype(int), name="Sell"), secondary_y=True)

    # for premium in range(200, 801, 100):
    #     signal = gift_basket_contents + premium
    #     fig.add_trace(go.Scatter(y=signal, name=f"Signal - {premium}"), secondary_y=False)

    fig.add_trace(go.Scatter(y=gift_basket_diff, name="Signal"), secondary_y=True)
    fig.add_trace(go.Scatter(y=gift_basket_diff_min, name="Signal min"), secondary_y=True)
    fig.add_trace(go.Scatter(y=gift_basket_diff_max, name="Signal max"), secondary_y=True)
    fig.add_trace(go.Scatter(y=gift_basket_diff_25, name="Signal 25"), secondary_y=True)
    fig.add_trace(go.Scatter(y=gift_basket_diff_75, name="Signal 75"), secondary_y=True)

    fig.update_layout(title_text=f"Day {day}")
    fig.show()

In [4]:
chocolate_value = 8000
strawberries_value = 4000
roses_value = 15000
gift_basket_value = 355

gift_basket_diff = all_gift_basket - 4 * all_chocolate - 6 * all_strawberries - all_roses - gift_basket_value
print(f"{gift_basket_diff.mean()=} {gift_basket_diff.std()=}")

roses_diff = all_gift_basket - 4 * all_chocolate - 6 * all_strawberries - gift_basket_value
print(f"{roses_diff.mean()=} {roses_diff.std()=}")

# strawberries_solo = (all_gift_basket - 4 * all_chocolate - all_roses - gift_basket_solo.mean()) / 6
# print("Strawberries", strawberries.mean(), strawberries.std())

# chocolate_solo = (all_gift_basket - 6 * all_strawberries - all_roses - gift_basket_solo.mean()) / 4
# print("Chocolate", chocolate_solo.mean(), chocolate_solo.std())

gift_basket_diff.mean()=25.517370967741936 gift_basket_diff.std()=75.63184000434623
roses_diff.mean()=14528.745612903225 roses_diff.std()=173.23411926502118


In [5]:
for day in range(3):
    prices = get_prices(3, day)

    chocolate = get_product_prices(prices, "CHOCOLATE")
    strawberries = get_product_prices(prices, "STRAWBERRIES")
    roses = get_product_prices(prices, "ROSES")
    gift_basket = get_product_prices(prices, "GIFT_BASKET")

    rolling_roses = pd.Series(roses).rolling(50).mean()

    signal = gift_basket - 4 * chocolate - 6 * strawberries - 355
    signal = signal - rolling_roses

    fig = make_subplots(specs=[[{"secondary_y": True}]])
    fig.add_trace(go.Scatter(y=chocolate / np.linalg.norm(chocolate), name="Chocolate"), secondary_y=False)
    fig.add_trace(go.Scatter(y=strawberries / np.linalg.norm(strawberries), name="Strawberries"), secondary_y=False)
    fig.add_trace(go.Scatter(y=roses / np.linalg.norm(roses), name="Roses"), secondary_y=False)
    fig.add_trace(go.Scatter(y=gift_basket / np.linalg.norm(gift_basket), name="Gift basket"), secondary_y=False)
    # fig.add_trace(go.Scatter(y=signal, name="Signal"), secondary_y=True)
    fig.update_layout(title_text=f"Day {day}")
    fig.show()

In [6]:
for day in range(3):
    prices = get_prices(3, day)

    chocolate = get_product_prices(prices, "CHOCOLATE")
    strawberries = get_product_prices(prices, "STRAWBERRIES")
    roses = get_product_prices(prices, "ROSES")
    gift_basket = get_product_prices(prices, "GIFT_BASKET")

    signal = gift_basket - 6 * strawberries - roses - 4 * 8000 - 355
    signal = pd.Series(signal).rolling(5).mean() > pd.Series(signal).rolling(50).mean()
    signal = signal.astype(int)

    fig = make_subplots(specs=[[{"secondary_y": True}]])
    fig.add_trace(go.Scatter(y=chocolate, name="Chocolate"), secondary_y=False)
    fig.add_trace(go.Scatter(y=signal, name="Signal"), secondary_y=True)
    fig.update_layout(title_text=f"Day {day}")
    fig.show()